## Exercise: ML Workflows

Do a train/test split on a Dataset, create a baseline model, and evaluate the result.  Optionally, try to beat this baseline model by training a linear regression model.

Run the following cell to set up our environment.

In [0]:
%run "./Includes/Classroom-Setup"

Initialized classroom variables & functions...

Datasets are already mounted to /mnt/training from wasbs://training@dbtrainwesteurope.blob.core.windows.net/

In [0]:
%fs ls dbfs:/databricks-datasets/bikeSharing/data-001/hour.csv

path name size modificationTime dbfs:/databricks-datasets/bikeSharing/data-001/hour.csv hour.csv 1156736 1455505275000

Created user-specific database

Using the database saifahmed_k_outlook_com_db .

All done!

### Step 1: Train/Test Split

Import the bike sharing dataset and take a look at what's in it.  This dataset contains number of bikes rented (`cnt`) by season, year, month, and hour and for a number of weather conditions.

In [0]:
bikeDF = (spark
  .read
  .option("header", True)
  .option("inferSchema", True)
  .csv("dbfs:/databricks-datasets/bikeSharing/data-001/hour.csv")
  .drop("instant", "dteday", "casual", "registered", "holiday", "weekday") # Drop unnecessary features
)

display(bikeDF)

season yr mnth hr workingday weathersit temp atemp hum windspeed cnt 1 0 1 0 0 1 0.24 0.2879 0.81 0.0 16 1 0 1 1 0 1 0.22 0.2727 0.8 0.0 40 1 0 1 2 0 1 0.22 0.2727 0.8 0.0 32 1 0 1 3 0 1 0.24 0.2879 0.75 0.0 13 1 0 1 4 0 1 0.24 0.2879 0.75 0.0 1 1 0 1 5 0 2 0.24 0.2576 0.75 0.0896 1 1 0 1 6 0 1 0.22 0.2727 0.8 0.0 2 1 0 1 7 0 1 0.2 0.2576 0.86 0.0 3 1 0 1 8 0 1 0.24 0.2879 0.75 0.0 8 1 0 1 9 0 1 0.32 0.3485 0.76 0.0 14 1 0 1 10 0 1 0.38 0.3939 0.76 0.2537 36 1 0 1 11 0 1 0.36 0.3333 0.81 0.2836 56 1 0 1 12 0 1 0.42 0.4242 0.77 0.2836 84 1 0 1 13 0 2 0.46 0.4545 0.72 0.2985 94 1 0 1 14 0 2 0.46 0.4545 0.72 0.2836 106 1 0 1 15 0 2 0.44 0.4394 0.77 0.2985 110 1 0 1 16 0 2 0.42 0.4242 0.82 0.2985 93 1 0 1 17 0 2 0.44 0.4394 0.82 0.2836 67 1 0 1 18 0 3 0.42 0.4242 0.88 0.2537 35 1 0 1 19 0 3 0.42 0.4242 0.88 0.2537 37 1 0 1 20 0 2 0.4 0.4091 0.87 0.2537 36 1 0 1 21 0 2 0.4 0.4091 0.87 0.194 34 1 0 1 22 0 2 0.4 0.4091 0.94 0.2239 28 1 0 1 23 0 2 0.46 0.4545 0.88 0.2985 39 1 0 1 0 0 2 0.46 0.4545 0.88 0.2985 17 1 0 1 1 0 2 0.44 0.4394 0.94 0.2537 17 1 0 1 2 0 2 0.42 0.4242 1.0 0.2836 9 1 0 1 3 0 2 0.46 0.4545 0.94 0.194 6 1 0 1 4 0 2 0.46 0.4545 0.94 0.194 3 1 0 1 6 0 3 0.42 0.4242 0.77 0.2985 2 1 0 1 7 0 2 0.4 0.4091 0.76 0.194 1 1 0 1 8 0 3 0.4 0.4091 0.71 0.2239 8 1 0 1 9 0 2 0.38 0.3939 0.76 0.2239 20 1 0 1 10 0 2 0.36 0.3485 0.81 0.2239 53 1 0 1 11 0 2 0.36 0.3333 0.71 0.2537 70 1 0 1 12 0 2 0.36 0.3333 0.66 0.2985 93 1 0 1 13 0 2 0.36 0.3485 0.66 0.1343 75 1 0 1 14 0 3 0.36 0.3485 0.76 0.194 59 1 0 1 15 0 3 0.34 0.3333 0.81 0.1642 74 1 0 1 16 0 3 0.34 0.3333 0.71 0.1642 76 1 0 1 17 0 1 0.34 0.3333 0.57 0.194 65 1 0 1 18 0 2 0.36 0.3333 0.46 0.3284 53 1 0 1 19 0 1 0.32 0.2879 0.42 0.4478 30 1 0 1 20 0 1 0.3 0.2727 0.39 0.3582 22 1 0 1 21 0 1 0.26 0.2273 0.44 0.3284 31 1 0 1 22 0 1 0.24 0.2121 0.44 0.2985 9 1 0 1 23 0 1 0.22 0.2273 0.47 0.1642 8 1 0 1 0 1 1 0.22 0.197 0.44 0.3582 5 1 0 1 1 1 1 0.2 0.1667 0.44 0.4179 2 1 0 1 4 1 1 0.16 0.1364 0.47 0.3881 1 1 0 1 5 1 1 0.16 0.1364 0.47 0.2836 3 1 0 1 6 1 1 0.14 0.1061 0.5 0.3881 30 1 0 1 7 1 1 0.14 0.1364 0.5 0.194 64 1 0 1 8 1 1 0.14 0.1212 0.5 0.2836 154 1 0 1 9 1 1 0.16 0.1364 0.43 0.3881 88 1 0 1 10 1 1 0.18 0.1667 0.43 0.2537 44 1 0 1 11 1 1 0.2 0.1818 0.4 0.3284 51 1 0 1 12 1 1 0.22 0.2121 0.35 0.2985 61 1 0 1 13 1 1 0.24 0.2121 0.35 0.2836 61 1 0 1 14 1 1 0.26 0.2424 0.3 0.2836 77 1 0 1 15 1 1 0.26 0.2424 0.3 0.2537 72 1 0 1 16 1 1 0.26 0.2424 0.3 0.2537 76 1 0 1 17 1 1 0.24 0.2273 0.3 0.2239 157 1 0 1 18 1 1 0.24 0.2576 0.32 0.1045 157 1 0 1 19 1 1 0.2 0.2576 0.47 0.0 110 1 0 1 20 1 1 0.2 0.2273 0.47 0.1045 52 1 0 1 21 1 1 0.18 0.197 0.64 0.1343 52 1 0 1 22 1 1 0.14 0.1515 0.69 0.1343 20 1 0 1 23 1 1 0.18 0.2121 0.55 0.1045 12 1 0 1 0 1 1 0.16 0.1818 0.55 0.1045 5 1 0 1 1 1 1 0.16 0.1818 0.59 0.1045 2 1 0 1 2 1 1 0.14 0.1515 0.63 0.1343 1 1 0 1 4 1 1 0.14 0.1818 0.63 0.0896 2 1 0 1 5 1 1 0.12 0.1515 0.68 0.1045 4 1 0 1 6 1 1 0.12 0.1515 0.74 0.1045 36 1 0 1 7 1 1 0.12 0.1515 0.74 0.1343 94 1 0 1 8 1 1 0.14 0.1515 0.69 0.1642 179 1 0 1 9 1 1 0.16 0.1515 0.64 0.2239 100 1 0 1 10 1 2 0.16 0.1364 0.69 0.3284 42 1 0 1 11 1 1 0.22 0.2121 0.51 0.2985 57 1 0 1 12 1 1 0.22 0.2273 0.51 0.1642 78 1 0 1 13 1 1 0.24 0.2273 0.56 0.194 97 1 0 1 14 1 1 0.26 0.2576 0.52 0.2239 63 1 0 1 15 1 1 0.28 0.2727 0.52 0.2537 65 1 0 1 16 1 1 0.3 0.2879 0.49 0.2537 83 1 0 1 17 1 1 0.28 0.2727 0.48 0.2239 212 1 0 1 18 1 1 0.26 0.2576 0.48 0.194 182 1 0 1 19 1 1 0.24 0.2576 0.48 0.1045 112 1 0 1 20 1 1 0.24 0.2576 0.48 0.1045 54 1 0 1 21 1 1 0.22 0.2727 0.64 0.0 48 1 0 1 22 1 1 0.22 0.2576 0.64 0.0896 35 1 0 1 23 1 1 0.2 0.2273 0.69 0.0896 11 1 0 1 0 1 1 0.2 0.2576 0.64 0.0 6 1 0 1 1 1 1 0.16 0.197 0.74 0.0896 6 1 0 1 2 1 1 0.16 0.197 0.74 0.0896 2 1 0 1 4 1 1 0.24 0.2273 0.48 0.2239 2 1 0 1 5 1 1 0.22 0.2273 0.47 0.1642 3 1 0 1 6 1 1 0.2 0.197 0.47 0.2239 33 1 0 1 7 1 1 0.18 0.1818 0.43 0.194 88 1 0 1 8 1 1 0.2 0.1818 0.4 0.2985 195 1 0 1 9 1 1 0.22 0.197 0.37 0.3284 115 1 0 1 10 1 1 0.22 0.197 0.37 0.

Perform a train/test split.  Put 70% of the data into `trainBikeDF` and 30% into `testBikeDF`.  Use a seed of `42` so you have the same split every time you perform the operation.

In [0]:
# TODO
trainBikeDF, testBikeDF = bikeDF.randomSplit([0.7, 0.3], seed=42)

In [0]:
# Define the dbTest function
def dbTest(test_name, expected, result):
    assert result == expected, f"Test {test_name} failed: expected {expected}, got {result}"

# TEST - Run this cell to test your solution
_traincount = trainBikeDF.count()
_testcount = testBikeDF.count()

dbTest("ML1-P-03-01-01", True, _traincount < 13000 and _traincount > 12000)
dbTest("ML1-P-03-01-02", True, _testcount < 5500 and _testcount > 4800)

print("Tests passed!")

Tests passed!


### Step 2: Create a Baseline Model

Calculate the average of the column `cnt` and save it to the variable `trainCnt`.  Then create a new DataFrame `bikeTestPredictionDF` that appends a new column `prediction` that's the value of `trainCnt`.

### Baseline Model Concept
Purpose of a Baseline Model:
The baseline model serves as a benchmark to assess whether more complex models provide meaningful improvements.
In the context of regression, this benchmark prediction can be as simple as using the average of the target variable across all observations in the training data.
By evaluating this simple prediction, practitioners get an idea of how well the model can perform without incorporating patterns or relationships between the input features and the target variable.
When to Use a Baseline Model:
At the start of the modeling process, to establish a straightforward reference for future comparisons.
To understand the variance in the target variable: if the baseline performs well, it may indicate limited room for improvement with more complex models.
In regression tasks, calculating the baseline as the average value of the target variable is particularly common and effective.

In [0]:
from pyspark.sql.functions import avg, lit

# Assuming trainBikeDF and testBikeDF are already defined
# Calculate the average count from the training dataset
avgTrainCnt = trainBikeDF.select(avg("cnt")).first()[0]

# Create a baseline model by adding a column with the average count to the test dataset
bikeTestPredictionDF = testBikeDF.withColumn("prediction", lit(avgTrainCnt))

# Display the resulting DataFrame
display(bikeTestPredictionDF)

season yr mnth hr workingday weathersit temp atemp hum windspeed cnt prediction 1 0 1 0 0 1 0.1 0.0758 0.42 0.3881 25 188.89937878044793 1 0 1 0 0 1 0.24 0.2879 0.81 0.0 16 188.89937878044793 1 0 1 0 0 2 0.18 0.197 0.51 0.1642 25 188.89937878044793 1 0 1 0 0 2 0.2 0.197 0.47 0.2239 17 188.89937878044793 1 0 1 0 1 1 0.12 0.1364 0.5 0.194 14 188.89937878044793 1 0 1 0 1 1 0.14 0.1212 0.59 0.2836 7 188.89937878044793 1 0 1 0 1 1 0.14 0.1667 0.59 0.1045 12 188.89937878044793 1 0 1 0 1 1 0.22 0.197 0.44 0.3582 5 188.89937878044793 1 0 1 0 1 2 0.16 0.1364 0.69 0.2836 9 188.89937878044793 1 0 1 0 1 2 0.2 0.197 0.64 0.194 17 188.89937878044793 1 0 1 0 1 2 0.2 0.2121 0.75 0.1343 9 188.89937878044793 1 0 1 0 1 2 0.24 0.2273 0.7 0.2537 21 188.89937878044793 1 0 1 1 0 1 0.04 0.0758 0.57 0.1045 13 188.89937878044793 1 0 1 1 0 1 0.1 0.0606 0.42 0.4627 12 188.89937878044793 1 0 1 1 0 1 0.22 0.2273 0.64 0.194 20 188.89937878044793 1 0 1 1 0 1 0.26 0.2727 0.56 0.1343 23 188.89937878044793 1 0 1 1 0 2 0.04 0.0 0.41 0.3881 12 188.89937878044793 1 0 1 1 0 2 0.44 0.4394 0.94 0.2537 17 188.89937878044793 1 0 1 1 1 1 0.12 0.1212 0.5 0.2836 1 188.89937878044793 1 0 1 1 1 1 0.14 0.1212 0.5 0.2836 2 188.89937878044793 1 0 1 1 1 1 0.16 0.1818 0.59 0.1045 2 188.89937878044793 1 0 1 1 1 1 0.16 0.197 0.74 0.0896 6 188.89937878044793 1 0 1 1 1 1 0.16 0.2273 0.64 0.0 4 188.89937878044793 1 0 1 1 1 1 0.22 0.2121 0.64 0.2537 7 188.89937878044793 1 0 1 1 1 2 0.16 0.1667 0.69 0.1642 5 188.89937878044793 1 0 1 1 1 2 0.24 0.2273 0.7 0.2537 6 188.89937878044793 1 0 1 1 1 2 0.24 0.2424 0.65 0.1343 5 188.89937878044793 1 0 1 2 0 1 0.22 0.2727 0.8 0.0 32 188.89937878044793 1 0 1 2 0 2 0.04 0.0303 0.41 0.2537 11 188.89937878044793 1 0 1 2 1 1 0.1 0.1212 0.54 0.1343 1 188.89937878044793 1 0 1 2 1 1 0.12 0.1212 0.5 0.2239 3 188.89937878044793 1 0 1 2 1 1 0.16 0.197 0.74 0.0896 2 188.89937878044793 1 0 1 2 1 1 0.22 0.2273 0.64 0.194 1 188.89937878044793 1 0 1 2 1 3 0.22 0.2273 0.93 0.1343 3 188.89937878044793 1 0 1 3 0 2 0.18 0.1818 0.43 0.194 2 188.89937878044793 1 0 1 3 1 1 0.22 0.2273 0.64 0.194 2 188.89937878044793 1 0 1 4 0 2 0.46 0.4545 0.94 0.194 3 188.89937878044793 1 0 1 4 1 1 0.14 0.1212 0.5 0.2537 4 188.89937878044793 1 0 1 4 1 1 0.14 0.1667 0.74 0.1045 1 188.89937878044793 1 0 1 4 1 1 0.14 0.1818 0.63 0.0896 2 188.89937878044793 1 0 1 4 1 2 0.16 0.197 0.64 0.0896 1 188.89937878044793 1 0 1 4 1 2 0.22 0.2576 0.87 0.0896 1 188.89937878044793 1 0 1 5 0 1 0.16 0.2273 0.59 0.0 1 188.89937878044793 1 0 1 5 0 2 0.16 0.1667 0.74 0.1642 5 188.89937878044793 1 0 1 5 1 1 0.14 0.1364 0.74 0.2239 9 188.89937878044793 1 0 1 5 1 1 0.18 0.1667 0.64 0.2836 8 188.89937878044793 1 0 1 5 1 2 0.22 0.2576 0.93 0.0896 7 188.89937878044793 1 0 1 5 1 3 0.22 0.2727 0.55 0.0 5 188.89937878044793 1 0 1 6 0 2 0.18 0.1818 0.43 0.194 5 188.89937878044793 1 0 1 6 1 1 0.1 0.1818 0.54 0.0 17 188.89937878044793 1 0 1 6 1 1 0.12 0.1515 0.93 0.1343 16 188.89937878044793 1 0 1 6 1 1 0.16 0.1818 0.74 0.1045 36 188.89937878044793 1 0 1 7 0 1 0.08 0.1061 0.58 0.1642 2 188.89937878044793 1 0 1 7 0 2 0.16 0.1818 0.74 0.1045 9 188.89937878044793 1 0 1 7 1 1 0.02 0.1212 0.48 0.0 84 188.89937878044793 1 0 1 7 1 1 0.2 0.2121 0.69 0.1343 84 188.89937878044793 1 0 1 7 1 2 0.16 0.1364 0.64 0.2836 72 188.89937878044793 1 0 1 7 1 2 0.16 0.2273 0.55 0.0 99 188.89937878044793 1 0 1 8 0 1 0.06 0.0758 0.62 0.1642 19 188.89937878044793 1 0 1 8 0 1 0.24 0.2879 0.75 0.0 8 188.89937878044793 1 0 1 8 0 3 0.16 0.1818 0.93 0.1045 15 188.89937878044793 1 0 1 8 1 1 0.14 0.1364 0.5 0.194 202 188.89937878044793 1 0 1 8 1 2 0.16 0.1364 0.59 0.2836 185 188.89937878044793 1 0 1 8 1 2 0.16 0.1818 0.74 0.1343 238 188.89937878044793 1 0 1 9 0 1 0.1 0.0758 0.54 0.3582 28 188.89937878044793 1 0 1 9 1 1 0.16 0.1364 0.59 0.3284 81 188.89937878044793 1 0 1 9 1 1 0.22 0.197 0.37 0.3284 115 188.89937878044793 1 0 1 9 1 2 0.18 0.197 0.51 0.1642 130 188.89937878044793 1 0 1 9 1 2 0.2 0.2273 0.64 0.0896 144 188.89937878044793 1 0 1 9 1 3 0.1

In [0]:
# TEST - Run this cell to test your solution
dbTest("ML1-P-03-02-01", True, avgTrainCnt < 195 and avgTrainCnt > 180)
dbTest("ML1-P-03-02-02", True, "prediction" in bikeTestPredictionDF.columns)

print("Tests passed!")

Tests passed!


### Step 3: Evaluate the Result

Evaluate the result using `mse` as the error metric.  Save the result to `testError`.

<img alt="Hint" title="Hint" style="vertical-align: text-bottom; position: relative; height:1.75em; top:0.3em" src="https://files.training.databricks.com/static/images/icon-light-bulb.svg"/>&nbsp;**Hint:** Your baseline prediction will not be very accurate.  Be sure to take the square root of the MSE to return the results to the proper units (that is, bike counts).

In [0]:
# TODO
from pyspark.ml.evaluation import RegressionEvaluator
evaluator = RegressionEvaluator(labelCol="cnt", predictionCol="prediction", metricName="mse")
testError = evaluator.evaluate(bikeTestPredictionDF)
print(testError)

33098.35537800063


In [0]:
# TEST - Run this cell to test your solution
dbTest("ML1-P-03-03-01", True, testError > 33000 and testError < 35000)

print("Tests passed!")

Tests passed!


### Step 4 (Optional): Beat the Baseline

Use a linear regression model (explored in the previous lesson) to beat the baseline model score.